In [1]:
# importing libraries for data modeling

import pandas as pd
import numpy as np
import collections
from nltk.tokenize.treebank import TreebankWordTokenizer
from nltk.tokenize import TweetTokenizer
from common import utils, vocabulary
from sklearn.model_selection import train_test_split
from sklearn.naive_bayes import MultinomialNB
from sklearn.metrics import accuracy_score
from sklearn.metrics import classification_report
from sklearn import preprocessing
import tensorflow as tf
import os
import time
import datetime
from CNN.text_cnn import TextCNN
from tensorflow.contrib import learn
import sys

/home/alexander_mpa/anaconda3/lib/python3.6/site-packages/h5py/__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters


In [2]:
# loading model data 

normal_train = pd.read_csv("data/wiki_matched_short.train.0", delimiter="\t", header = None, names = ['sentence_text'])
simple_train = pd.read_csv("data/wiki_matched_short.train.1", delimiter="\t", header = None, names = ['sentence_text'])
normal_test = pd.read_csv("data/wiki_matched_short.test.0", delimiter="\t", header = None, names = ['sentence_text'])
simple_test = pd.read_csv("data/wiki_matched_short.test.0", delimiter="\t", header = None, names = ['sentence_text'])


normal_simple_style_test = pd.DataFrame(data = open("data/wiki_matched.test.0.tsf.normal-simple").readlines(), columns = ['sentence_text'])

simple_normal_style_test = pd.DataFrame(data = open("data/wiki_matched.test.1.tsf.simple-normal").readlines(), columns = ['sentence_text'])

normal_train['party']='normal'
normal_test['party']='normal'
simple_train['party']='simple'
simple_test['party']='simple'

normal_simple_style_test['party']='simple'
simple_normal_style_test['party']='normal'

#combine data together for training/testing
#shuffle it for random order
all_train = normal_train.append(simple_train)
all_test = normal_test.append(simple_test)

all_style_test = normal_simple_style_test.append(simple_normal_style_test)

all_train = all_train.sample(frac=.25)
all_test = all_test.sample(frac=.1)

all_style_test = all_style_test.sample(frac=.1)

print(all_train.head())
print(all_test.head())
print(all_style_test.head())

                                            sentence_text   party
187892  originally , a firewall was a wall that was bu...  simple
100871  for example , he noticed that the wings of dra...  normal
154588  it was the venue of the first NP one NP NP NP ...  simple
96199                   NP was published in NP DGDGDGDG .  simple
53394                        list on NP ' s NP web page .  normal
                                         sentence_text   party
51   he is also a member of another NP boyband DGDG...  normal
60   they are castrated so that the animal may be m...  normal
151  the lawyer , NP ( NP NP ) , became his idol , ...  simple
244  a mutant is a type of fictional character that...  simple
230           NP is a city in NP NP , NP , NP states .  simple
                                         sentence_text   party
15   it is the second role of the NP of NP , NP , N...  normal
326  NP ' s ` ` <unk> ' ' , ` ` <unk> ' ' , ` ` <un...  normal
55   NP is the second of the ` ` <unk

In [3]:
train_x = all_train['sentence_text']
train_y = all_train['party']
test_x = all_test['sentence_text']
test_y = all_test['party']

style_test_x = all_style_test['sentence_text']
style_test_y = all_style_test['party']

In [4]:
# tokenize data in comment body

tokenizer = TweetTokenizer()

train_x_tokens = []
test_x_tokens = []
style_test_x_tokens = []

for x in train_x:
    train_x_tokens.append(tokenizer.tokenize(x))
    
for x in test_x:
    test_x_tokens.append(tokenizer.tokenize(x))
    
for x in style_test_x:
    style_test_x_tokens.append(tokenizer.tokenize(x))

In [5]:
# define vocabulary using w266 common vocab

train_text_all = [item for sublist in train_x_tokens for item in sublist]

vocab = vocabulary.Vocabulary(train_text_all, size=20000)
print("Vocabulary size: {:,}".format(vocab.size))
print("Vocabulary dict: ", vocab.word_to_id)

train_x_ids = []
test_x_ids = []
style_test_x_ids = []

for x in train_x_tokens:
    train_x_ids.append(vocab.words_to_ids(x))
    
for x in test_x_tokens:
    test_x_ids.append(vocab.words_to_ids(x))
    
for x in style_test_x_tokens:
    style_test_x_ids.append(vocab.words_to_ids(x))

Vocabulary size: 20,000
Vocabulary dict:  {'<s>': 0, '</s>': 1, '<unk>': 2, 'NP': 3, 'the': 4, '.': 5, ',': 6, 'of': 7, 'in': 8, 'and': 9, 'a': 10, 'to': 11, "'": 12, 'is': 13, 'DGDGDGDG': 14, 'was': 15, '`': 16, ')': 17, '(': 18, 'on': 19, 'as': 20, 'for': 21, 'DGDG': 22, 'by': 23, 'he': 24, 'it': 25, 'are': 26, 'with': 27, 's': 28, 'that': 29, 'from': 30, 'his': 31, 'at': 32, 'an': 33, 'DG': 34, 'or': 35, 'also': 36, 'were': 37, 'this': 38, 'be': 39, 'has': 40, 'which': 41, 'first': 42, 'have': 43, 'they': 44, 'one': 45, 'not': 46, 'had': 47, 'after': 48, 'their': 49, 'its': 50, ':': 51, 'other': 52, 'her': 53, 'she': 54, 'can': 55, 'but': 56, 'DGDGDG': 57, 'used': 58, 'two': 59, 'most': 60, 'when': 61, 'there': 62, '-': 63, 'many': 64, 'called': 65, 'some': 66, 'been': 67, 'who': 68, 'made': 69, 'all': 70, 'more': 71, 'into': 72, 'known': 73, 'became': 74, 'people': 75, 'time': 76, 'only': 77, 'during': 78, 'about': 79, 'years': 80, 'born': 81, 'these': 82, 'than': 83, 'later': 84, 

In [6]:
# count token occurences and convert to feature vector for BoW model

train_x_fdict = []
test_x_fdict = []
style_test_x_fdict = []

for x in train_x_ids:
    train_x_fdict.append(collections.Counter(x))
    
for x in test_x_ids:
    test_x_fdict.append(collections.Counter(x))
    
for x in style_test_x_ids:
    # remove democrat/republican tag from style test data
    del x[0]
    style_test_x_fdict.append(collections.Counter(x))

train_x_vector = []
test_x_vector = []
style_test_x_vector = []

num_features = vocab.size
print('creating id lists...')
for x in train_x_fdict:
    train_x_vector.append([x.get(i, 0) for i in range(num_features)])
    
for x in test_x_fdict:
    test_x_vector.append([x.get(i, 0) for i in range(num_features)])
    
for x in style_test_x_fdict:
    style_test_x_vector.append([x.get(i, 0) for i in range(num_features)])

# use w266 common utils to convert id lists to sparse bow matrix
print('starting id lists to sparse bow conversion...')
train_x_sparse_bow = utils.id_lists_to_sparse_bow(train_x_fdict, vocab.size)
test_x_sparse_bow = utils.id_lists_to_sparse_bow(test_x_fdict, vocab.size)
style_test_x_sparse_bow = utils.id_lists_to_sparse_bow(style_test_x_fdict, vocab.size)

# training Multinomial Naive Bayes for simple baseline model
print('training Multinomial Naive Bayes for simple baseline model...')
nb = MultinomialNB()
nb.fit(train_x_sparse_bow, train_y)
y_pred = nb.predict(test_x_sparse_bow)
y_pred_style = nb.predict(style_test_x_sparse_bow)

acc = accuracy_score(test_y, y_pred)
print("Accuracy on test set: {:.02%}".format(acc))
classrep = classification_report(test_y, y_pred)
print(classrep)

acc_style = accuracy_score(style_test_y, y_pred_style)
print("Accuracy on style test set: {:.02%}".format(acc_style))
classrep_style = classification_report(style_test_y, y_pred_style)
print(classrep_style)

creating id lists...
starting id lists to sparse bow conversion...
training Multinomial Naive Bayes for simple baseline model...
Accuracy on test set: 56.36%
             precision    recall  f1-score   support

     normal       0.58      0.66      0.61        29
     simple       0.55      0.46      0.50        26

avg / total       0.56      0.56      0.56        55

Accuracy on style test set: 48.61%
             precision    recall  f1-score   support

     normal       0.50      0.49      0.49        37
     simple       0.47      0.49      0.48        35

avg / total       0.49      0.49      0.49        72



In [7]:
# pad all id vectors to max length for Neural model

max_comment_length = max([len(x) for x in train_x_ids])

train_x_neural = train_x_ids
test_x_neural = test_x_ids
style_test_x_neural = style_test_x_ids

for x in train_x_neural:
    # remove democrat/republican tag from train data
    del x[0]
    if len(x) < max_comment_length:
        for n in range(max_comment_length - len(x)):
            x.append(1)
    elif len(x) > max_comment_length:
        x = x[:max_comment_length]
        
for x in test_x_neural:
    if len(x) < max_comment_length:
        for n in range(max_comment_length - len(x)):
            x.append(1)
    elif len(x) > max_comment_length:
        x = x[:max_comment_length]
        
for x in style_test_x_neural:
    if len(x) < max_comment_length:
        for n in range(max_comment_length - len(x)):
            x.append(1)
    elif len(x) > max_comment_length:
        x = x[:max_comment_length]

# convert labels to one-hot vectors for Neural model --update your class lables below!!

terms_list = [['normal'],['simple']]
lb = preprocessing.MultiLabelBinarizer()
lb.fit(terms_list)

train_labels = np.array(train_y.tolist())
test_labels = np.array(test_y.tolist())
style_test_labels = np.array(style_test_y.tolist())

train_lables_format = [train_labels[i:i+1] for i in range(0, len(train_labels), 1)]    
test_lables_format = [test_labels[i:i+1] for i in range(0, len(test_labels), 1)]
style_test_lables_format = [style_test_labels[i:i+1] for i in range(0, len(style_test_labels), 1)]

train_y_neural = lb.transform(train_lables_format)
test_y_neural = lb.transform(test_lables_format)
style_test_y_neural = lb.transform(test_lables_format)

In [8]:
# creating and training CNN for deep classification
# CNN model structure and code based on an implementation of Kim Yoon's "Convolutional Neural Networks for Sentence Classification"
# From https://github.com/dennybritz/cnn-text-classification-tf

# run this to clear tf flags without re-starting kernel

def del_all_flags(FLAGS):
    flags_dict = FLAGS._flags()
    keys_list = [keys for keys in flags_dict]
    for keys in keys_list:
        FLAGS.__delattr__(keys)
        
del_all_flags(tf.flags.FLAGS)

# Parameters
# ==================================================

# Model Hyperparameters
tf.flags.DEFINE_integer("embedding_dim", 128, "Dimensionality of character embedding (default: 128)")
tf.flags.DEFINE_string("filter_sizes", "1,2,3,4,5", "Comma-separated filter sizes (default: '3,4,5')")
tf.flags.DEFINE_integer("num_filters", 128, "Number of filters per filter size (default: 128)")
tf.flags.DEFINE_float("dropout_keep_prob", 0.5, "Dropout keep probability (default: 0.5)")
tf.flags.DEFINE_float("l2_reg_lambda", 0.0, "L2 regularization lambda (default: 0.0)")

# Training parameters
tf.flags.DEFINE_integer("batch_size", 64, "Batch Size (default: 64)")
tf.flags.DEFINE_integer("num_epochs", 50, "Number of training epochs (default: 200)")
tf.flags.DEFINE_integer("evaluate_every", 100, "Evaluate model on dev set after this many steps (default: 100)")
tf.flags.DEFINE_integer("checkpoint_every", 100, "Save model after this many steps (default: 100)")
tf.flags.DEFINE_integer("num_checkpoints", 5, "Number of checkpoints to store (default: 5)")

# Misc Parameters
tf.flags.DEFINE_boolean("allow_soft_placement", True, "Allow device soft device placement")
tf.flags.DEFINE_boolean("log_device_placement", False, "Log placement of ops on devices")
tf.app.flags.DEFINE_string('f', '', 'kernel')

FLAGS = tf.flags.FLAGS
FLAGS(sys.argv)
print("\nParameters:")
for attr, value in sorted(FLAGS.__flags.items()):
    print("{}={}".format(attr.upper(), value))
print("")


# Data Preparation
# ==================================================

x_train = np.array(train_x_neural)
y_train = np.array(train_y_neural)
x_dev = np.array(test_x_neural)
y_dev = np.array(test_y_neural)

print("x_train", np.shape(x_train))
print("y_train", np.shape(y_train))
print("x_dev", np.shape(x_dev))
print("x_dev", np.shape(y_dev))

print("Vocabulary Size: {:d}".format(vocab.size))
print("Train/Dev split: {:d}/{:d}".format(len(y_train), len(y_dev)))


# Training
# ==================================================

def batch_iter(data, batch_size, num_epochs, shuffle=True):
    """
    Generates a batch iterator for a dataset.
    """
    data = np.array(data)
    data_size = len(data)
    num_batches_per_epoch = int((len(data)-1)/batch_size) + 1
    for epoch in range(num_epochs):
        # Shuffle the data at each epoch
        if shuffle:
            shuffle_indices = np.random.permutation(np.arange(data_size))
            shuffled_data = data[shuffle_indices]
        else:
            shuffled_data = data
        for batch_num in range(num_batches_per_epoch):
            start_index = batch_num * batch_size
            end_index = min((batch_num + 1) * batch_size, data_size)
            yield shuffled_data[start_index:end_index]
            
with tf.Graph().as_default():
    session_conf = tf.ConfigProto(
      allow_soft_placement=FLAGS.allow_soft_placement,
      log_device_placement=FLAGS.log_device_placement)
    sess = tf.Session(config=session_conf)
    with sess.as_default():
        cnn = TextCNN(
            sequence_length=x_train.shape[1],
            num_classes=2,
            vocab_size=vocab.size,
            embedding_size=FLAGS.embedding_dim,
            filter_sizes=list(map(int, FLAGS.filter_sizes.split(","))),
            num_filters=FLAGS.num_filters,
            l2_reg_lambda=FLAGS.l2_reg_lambda)

        # Define Training procedure
        global_step = tf.Variable(0, name="global_step", trainable=False)
        optimizer = tf.train.AdamOptimizer(1e-3)
        grads_and_vars = optimizer.compute_gradients(cnn.loss)
        train_op = optimizer.apply_gradients(grads_and_vars, global_step=global_step)

        # Keep track of gradient values and sparsity (optional)
        grad_summaries = []
        for g, v in grads_and_vars:
            if g is not None:
                grad_hist_summary = tf.summary.histogram("{}/grad/hist".format(v.name), g)
                sparsity_summary = tf.summary.scalar("{}/grad/sparsity".format(v.name), tf.nn.zero_fraction(g))
                grad_summaries.append(grad_hist_summary)
                grad_summaries.append(sparsity_summary)
        grad_summaries_merged = tf.summary.merge(grad_summaries)

        # Output directory for models and summaries
        timestamp = str(int(time.time()))
        out_dir = os.path.abspath(os.path.join(os.path.curdir, "runs", timestamp))
        print("Writing to {}\n".format(out_dir))

        # Summaries for loss and accuracy
        loss_summary = tf.summary.scalar("loss", cnn.loss)
        acc_summary = tf.summary.scalar("accuracy", cnn.accuracy)

        # Train Summaries
        train_summary_op = tf.summary.merge([loss_summary, acc_summary, grad_summaries_merged])
        train_summary_dir = os.path.join(out_dir, "summaries", "train")
        train_summary_writer = tf.summary.FileWriter(train_summary_dir, sess.graph)

        # Dev summaries
        dev_summary_op = tf.summary.merge([loss_summary, acc_summary])
        dev_summary_dir = os.path.join(out_dir, "summaries", "dev")
        dev_summary_writer = tf.summary.FileWriter(dev_summary_dir, sess.graph)

        # Checkpoint directory. Tensorflow assumes this directory already exists so we need to create it
        checkpoint_dir = os.path.abspath(os.path.join(out_dir, "checkpoints"))
        checkpoint_prefix = os.path.join(checkpoint_dir, "model")
        if not os.path.exists(checkpoint_dir):
            os.makedirs(checkpoint_dir)
        saver = tf.train.Saver(tf.global_variables(), max_to_keep=FLAGS.num_checkpoints)

        # Initialize all variables
        sess.run(tf.global_variables_initializer())

        def train_step(x_batch, y_batch):
            """
            A single training step
            """
            feed_dict = {
              cnn.input_x: x_batch,
              cnn.input_y: y_batch,
              cnn.dropout_keep_prob: FLAGS.dropout_keep_prob
            }
            _, step, summaries, loss, accuracy = sess.run(
                [train_op, global_step, train_summary_op, cnn.loss, cnn.accuracy],
                feed_dict)
            time_str = datetime.datetime.now().isoformat()
            print("{}: step {}, loss {:g}, acc {:g}".format(time_str, step, loss, accuracy))
            train_summary_writer.add_summary(summaries, step)

        def dev_step(x_batch, y_batch, writer=None):
            """
            Evaluates model on a dev set
            """
            feed_dict = {
              cnn.input_x: x_batch,
              cnn.input_y: y_batch,
              cnn.dropout_keep_prob: 1.0
            }
            step, summaries, loss, accuracy = sess.run(
                [global_step, dev_summary_op, cnn.loss, cnn.accuracy],
                feed_dict)
            time_str = datetime.datetime.now().isoformat()
            print("{}: step {}, loss {:g}, acc {:g}".format(time_str, step, loss, accuracy))
            if writer:
                writer.add_summary(summaries, step)

        # Generate batches
        batches = batch_iter(
            list(zip(x_train, y_train)), FLAGS.batch_size, FLAGS.num_epochs)
        # Training loop. For each batch...
        for batch in batches:
            x_batch, y_batch = zip(*batch)
            train_step(x_batch, y_batch)
            current_step = tf.train.global_step(sess, global_step)
            if current_step % FLAGS.evaluate_every == 0:
                print("\nEvaluation:")
                dev_step(x_dev, y_dev, writer=dev_summary_writer)
                print("")
            if current_step % FLAGS.checkpoint_every == 0:
                path = saver.save(sess, checkpoint_prefix, global_step=current_step)
                print("Saved model checkpoint to {}\n".format(path))


Parameters:
ALLOW_SOFT_PLACEMENT=<absl.flags._flag.BooleanFlag object at 0x7f6434274ac8>
BATCH_SIZE=<absl.flags._flag.Flag object at 0x7f64342746d8>
CHECKPOINT_EVERY=<absl.flags._flag.Flag object at 0x7f6434274898>
DROPOUT_KEEP_PROB=<absl.flags._flag.Flag object at 0x7f6434274668>
EMBEDDING_DIM=<absl.flags._flag.Flag object at 0x7f6434274438>
EVALUATE_EVERY=<absl.flags._flag.Flag object at 0x7f64342747f0>
F=<absl.flags._flag.Flag object at 0x7f6434274ba8>
FILTER_SIZES=<absl.flags._flag.Flag object at 0x7f6434274390>
L2_REG_LAMBDA=<absl.flags._flag.Flag object at 0x7f64342745c0>
LOG_DEVICE_PLACEMENT=<absl.flags._flag.BooleanFlag object at 0x7f6434274b70>
NUM_CHECKPOINTS=<absl.flags._flag.Flag object at 0x7f6434274940>
NUM_EPOCHS=<absl.flags._flag.Flag object at 0x7f6434274748>
NUM_FILTERS=<absl.flags._flag.Flag object at 0x7f64342744e0>

x_train (94368, 176)
y_train (94368, 2)
x_dev (55, 176)
x_dev (55, 2)
Vocabulary Size: 20000
Train/Dev split: 94368/55
Instructions for updating:

Fut

2018-08-06T19:17:40.064266: step 63, loss 1.26062, acc 0.5625
2018-08-06T19:17:40.131889: step 64, loss 1.38795, acc 0.59375
2018-08-06T19:17:40.195957: step 65, loss 1.95359, acc 0.484375
2018-08-06T19:17:40.258781: step 66, loss 1.4331, acc 0.5
2018-08-06T19:17:40.320839: step 67, loss 1.09984, acc 0.53125
2018-08-06T19:17:40.387039: step 68, loss 1.81663, acc 0.421875
2018-08-06T19:17:40.450712: step 69, loss 1.67243, acc 0.5
2018-08-06T19:17:40.513700: step 70, loss 1.51064, acc 0.484375
2018-08-06T19:17:40.576096: step 71, loss 1.54758, acc 0.5
2018-08-06T19:17:40.640337: step 72, loss 1.45512, acc 0.546875
2018-08-06T19:17:40.705924: step 73, loss 1.53999, acc 0.453125
2018-08-06T19:17:40.770733: step 74, loss 1.12119, acc 0.609375
2018-08-06T19:17:40.835075: step 75, loss 1.23897, acc 0.5
2018-08-06T19:17:40.900238: step 76, loss 1.07906, acc 0.59375
2018-08-06T19:17:40.966020: step 77, loss 1.36955, acc 0.484375
2018-08-06T19:17:41.028534: step 78, loss 1.34644, acc 0.53125
201

2018-08-06T19:17:48.524930: step 190, loss 0.978647, acc 0.53125
2018-08-06T19:17:48.590874: step 191, loss 1.07888, acc 0.625
2018-08-06T19:17:48.656818: step 192, loss 1.10488, acc 0.453125
2018-08-06T19:17:48.723965: step 193, loss 1.19842, acc 0.421875
2018-08-06T19:17:48.787798: step 194, loss 1.24745, acc 0.390625
2018-08-06T19:17:48.854078: step 195, loss 0.866548, acc 0.625
2018-08-06T19:17:48.917862: step 196, loss 0.864582, acc 0.5625
2018-08-06T19:17:48.981811: step 197, loss 0.912589, acc 0.546875
2018-08-06T19:17:49.046281: step 198, loss 1.14439, acc 0.5
2018-08-06T19:17:49.109660: step 199, loss 0.965357, acc 0.578125
2018-08-06T19:17:49.176251: step 200, loss 1.18535, acc 0.46875

Evaluation:
2018-08-06T19:17:49.184735: step 200, loss 0.85044, acc 0.472727

Saved model checkpoint to /home/alexander_mpa/capstone/Parlancr/models/classifier/runs/1533583054/checkpoints/model-200

2018-08-06T19:17:49.354854: step 201, loss 0.8358, acc 0.625
2018-08-06T19:17:49.416665: step 2

2018-08-06T19:17:56.754017: step 314, loss 1.02967, acc 0.484375
2018-08-06T19:17:56.818226: step 315, loss 0.830433, acc 0.484375
2018-08-06T19:17:56.882559: step 316, loss 0.807889, acc 0.640625
2018-08-06T19:17:56.948412: step 317, loss 0.863263, acc 0.5625
2018-08-06T19:17:57.011865: step 318, loss 0.832158, acc 0.546875
2018-08-06T19:17:57.078281: step 319, loss 0.978855, acc 0.5
2018-08-06T19:17:57.145153: step 320, loss 0.803255, acc 0.53125
2018-08-06T19:17:57.209969: step 321, loss 1.08668, acc 0.390625
2018-08-06T19:17:57.273717: step 322, loss 0.735903, acc 0.53125
2018-08-06T19:17:57.339376: step 323, loss 0.826878, acc 0.53125
2018-08-06T19:17:57.406525: step 324, loss 0.792766, acc 0.640625
2018-08-06T19:17:57.471269: step 325, loss 0.958217, acc 0.46875
2018-08-06T19:17:57.536112: step 326, loss 0.740417, acc 0.59375
2018-08-06T19:17:57.605628: step 327, loss 0.776182, acc 0.53125
2018-08-06T19:17:57.669837: step 328, loss 0.845088, acc 0.4375
2018-08-06T19:17:57.735455:

2018-08-06T19:18:05.025374: step 439, loss 0.739667, acc 0.546875
2018-08-06T19:18:05.090053: step 440, loss 0.71631, acc 0.46875
2018-08-06T19:18:05.155580: step 441, loss 0.763207, acc 0.515625
2018-08-06T19:18:05.219451: step 442, loss 0.785614, acc 0.5625
2018-08-06T19:18:05.284338: step 443, loss 0.652954, acc 0.671875
2018-08-06T19:18:05.349137: step 444, loss 0.76757, acc 0.421875
2018-08-06T19:18:05.412531: step 445, loss 0.75271, acc 0.59375
2018-08-06T19:18:05.476923: step 446, loss 0.718822, acc 0.546875
2018-08-06T19:18:05.544837: step 447, loss 0.738838, acc 0.515625
2018-08-06T19:18:05.607351: step 448, loss 0.75555, acc 0.484375
2018-08-06T19:18:05.670254: step 449, loss 0.736436, acc 0.578125
2018-08-06T19:18:05.735243: step 450, loss 0.756522, acc 0.484375
2018-08-06T19:18:05.796838: step 451, loss 0.741465, acc 0.515625
2018-08-06T19:18:05.860571: step 452, loss 0.71125, acc 0.609375
2018-08-06T19:18:05.923176: step 453, loss 0.806891, acc 0.453125
2018-08-06T19:18:05

...

2018-08-06T20:12:16.762333: step 49731, loss 0.13334, acc 0.953125
2018-08-06T20:12:16.825012: step 49732, loss 0.159119, acc 0.90625
2018-08-06T20:12:16.889888: step 49733, loss 0.165542, acc 0.921875
2018-08-06T20:12:16.952187: step 49734, loss 0.242571, acc 0.9375
2018-08-06T20:12:17.016789: step 49735, loss 0.287615, acc 0.890625
2018-08-06T20:12:17.083770: step 49736, loss 0.132389, acc 0.9375
2018-08-06T20:12:17.148861: step 49737, loss 0.198014, acc 0.890625
2018-08-06T20:12:17.212729: step 49738, loss 0.127221, acc 0.953125
2018-08-06T20:12:17.277300: step 49739, loss 0.220728, acc 0.875
2018-08-06T20:12:17.342827: step 49740, loss 0.176581, acc 0.890625
2018-08-06T20:12:17.406192: step 49741, loss 0.118039, acc 0.96875
2018-08-06T20:12:17.471761: step 49742, loss 0.193502, acc 0.953125
2018-08-06T20:12:17.535846: step 49743, loss 0.30262, acc 0.890625
2018-08-06T20:12:17.600587: step 49744, loss 0.173803, acc 0.9375
2018-08-06T20:12:17.663245: step 49745, loss 0.300834, acc 0.

2018-08-06T20:12:24.721138: step 49852, loss 0.229927, acc 0.875
2018-08-06T20:12:24.785375: step 49853, loss 0.174258, acc 0.90625
2018-08-06T20:12:24.850816: step 49854, loss 0.197531, acc 0.921875
2018-08-06T20:12:24.918283: step 49855, loss 0.118866, acc 0.953125
2018-08-06T20:12:24.981443: step 49856, loss 0.254683, acc 0.875
2018-08-06T20:12:25.047315: step 49857, loss 0.215215, acc 0.921875
2018-08-06T20:12:25.110424: step 49858, loss 0.144278, acc 0.953125
2018-08-06T20:12:25.171811: step 49859, loss 0.223145, acc 0.890625
2018-08-06T20:12:25.237295: step 49860, loss 0.18764, acc 0.921875
2018-08-06T20:12:25.301643: step 49861, loss 0.183761, acc 0.90625
2018-08-06T20:12:25.365908: step 49862, loss 0.108943, acc 0.9375
2018-08-06T20:12:25.427965: step 49863, loss 0.241772, acc 0.921875
2018-08-06T20:12:25.491631: step 49864, loss 0.399647, acc 0.890625
2018-08-06T20:12:25.555205: step 49865, loss 0.140885, acc 0.953125
2018-08-06T20:12:25.618932: step 49866, loss 0.182787, acc 

2018-08-06T20:12:32.733686: step 49973, loss 0.109041, acc 0.953125
2018-08-06T20:12:32.798718: step 49974, loss 0.207528, acc 0.890625
2018-08-06T20:12:32.863198: step 49975, loss 0.181039, acc 0.921875
2018-08-06T20:12:32.930293: step 49976, loss 0.147696, acc 0.9375
2018-08-06T20:12:32.995225: step 49977, loss 0.170315, acc 0.921875
2018-08-06T20:12:33.061901: step 49978, loss 0.211204, acc 0.9375
2018-08-06T20:12:33.125985: step 49979, loss 0.0884829, acc 0.984375
2018-08-06T20:12:33.191518: step 49980, loss 0.232446, acc 0.859375
2018-08-06T20:12:33.258987: step 49981, loss 0.132378, acc 0.9375
2018-08-06T20:12:33.323054: step 49982, loss 0.195898, acc 0.90625
2018-08-06T20:12:33.387392: step 49983, loss 0.142956, acc 0.90625
2018-08-06T20:12:33.450734: step 49984, loss 0.317542, acc 0.921875
2018-08-06T20:12:33.515703: step 49985, loss 0.213782, acc 0.921875
2018-08-06T20:12:33.577338: step 49986, loss 0.23536, acc 0.9375
2018-08-06T20:12:33.641672: step 49987, loss 0.1521, acc 0

2018-08-06T20:12:40.708725: step 50094, loss 0.154347, acc 0.875
2018-08-06T20:12:40.771784: step 50095, loss 0.190961, acc 0.90625
2018-08-06T20:12:40.836900: step 50096, loss 0.302369, acc 0.875
2018-08-06T20:12:40.901104: step 50097, loss 0.185767, acc 0.921875
2018-08-06T20:12:40.968402: step 50098, loss 0.105705, acc 0.96875
2018-08-06T20:12:41.032437: step 50099, loss 0.246757, acc 0.921875
2018-08-06T20:12:41.098628: step 50100, loss 0.183927, acc 0.9375

Evaluation:
2018-08-06T20:12:41.107698: step 50100, loss 3.57983, acc 0.527273

Saved model checkpoint to /home/alexander_mpa/capstone/Parlancr/models/classifier/runs/1533583054/checkpoints/model-50100

2018-08-06T20:12:41.275029: step 50101, loss 0.12254, acc 0.953125
2018-08-06T20:12:41.338297: step 50102, loss 0.255109, acc 0.859375
2018-08-06T20:12:41.404991: step 50103, loss 0.311407, acc 0.90625
2018-08-06T20:12:41.469491: step 50104, loss 0.230696, acc 0.90625
2018-08-06T20:12:41.533305: step 50105, loss 0.139451, acc 0.

KeyboardInterrupt: 

In [10]:
# running CNN model against style transferred test data

# run this to clear tf flags without re-starting kernel

def del_all_flags(FLAGS):
    flags_dict = FLAGS._flags()
    keys_list = [keys for keys in flags_dict]
    for keys in keys_list:
        FLAGS.__delattr__(keys)
        
del_all_flags(tf.flags.FLAGS)

# Eval Parameters
# Update these checkpoint locations of the latest model from the log output of the cell above
tf.flags.DEFINE_string("checkpoint_dir", "/home/alexander_mpa/capstone/Parlancr/models/classifier/runs/1533583054/checkpoints/", "Checkpoint directory from training run")
checkpoint_file = "/home/alexander_mpa/capstone/Parlancr/models/classifier/runs/1533583054/checkpoints/model-50100"

# Misc Parameters
tf.flags.DEFINE_boolean("allow_soft_placement", True, "Allow device soft device placement")
tf.flags.DEFINE_boolean("log_device_placement", False, "Log placement of ops on devices")
tf.flags.DEFINE_integer("batch_size", 64, "Batch Size (default: 64)")
tf.app.flags.DEFINE_string('f', '', 'kernel')

FLAGS = tf.flags.FLAGS
FLAGS(sys.argv)
print("\nParameters:")
for attr, value in sorted(FLAGS.__flags.items()):
    print("{}={}".format(attr.upper(), value))
print("")

x_test = np.array(style_test_x_neural)
y_test = np.array(style_test_y_neural)


print("\nEvaluating...\n")

# Evaluation
# ==================================================
def batch_iter(data, batch_size, num_epochs, shuffle=True):
    """
    Generates a batch iterator for a dataset.
    """
    data = np.array(data)
    data_size = len(data)
    num_batches_per_epoch = int((len(data)-1)/batch_size) + 1
    for epoch in range(num_epochs):
        # Shuffle the data at each epoch
        if shuffle:
            shuffle_indices = np.random.permutation(np.arange(data_size))
            shuffled_data = data[shuffle_indices]
        else:
            shuffled_data = data
        for batch_num in range(num_batches_per_epoch):
            start_index = batch_num * batch_size
            end_index = min((batch_num + 1) * batch_size, data_size)
            yield shuffled_data[start_index:end_index]

graph = tf.Graph()
with graph.as_default():
    session_conf = tf.ConfigProto(
      allow_soft_placement=FLAGS.allow_soft_placement,
      log_device_placement=FLAGS.log_device_placement)
    sess = tf.Session(config=session_conf)
    with sess.as_default():
        # Load the saved meta graph and restore variables
        saver = tf.train.import_meta_graph("{}.meta".format(checkpoint_file))
        saver.restore(sess, checkpoint_file)

        # Get the placeholders from the graph by name
        input_x = graph.get_operation_by_name("input_x").outputs[0]
        # input_y = graph.get_operation_by_name("input_y").outputs[0]
        dropout_keep_prob = graph.get_operation_by_name("dropout_keep_prob").outputs[0]

        # Tensors we want to evaluate
        predictions = graph.get_operation_by_name("output/predictions").outputs[0]

        # Generate batches for one epoch
        batches = batch_iter(list(x_test), FLAGS.batch_size, 1, shuffle=False)

        # Collect the predictions here
        all_predictions = []

        for x_test_batch in batches:
            batch_predictions = sess.run(predictions, {input_x: x_test_batch, dropout_keep_prob: 1.0})
            all_predictions = np.concatenate([all_predictions, batch_predictions])

# Print accuracy

lb = preprocessing.LabelBinarizer(neg_label=0, pos_label=1, sparse_output=False)
lb.fit(np.asarray(style_test_y.tolist()).flatten())  
style_test_y_neural_acc = lb.transform(np.asarray(style_test_y.tolist()))

acc_style_neural = accuracy_score(style_test_y_neural_acc, all_predictions)
print("Accuracy on style test set: {:.02%}".format(acc_style_neural))
classrep_style_neural = classification_report(style_test_y_neural_acc, all_predictions)
print(classrep_style)


Parameters:
ALLOW_SOFT_PLACEMENT=<absl.flags._flag.BooleanFlag object at 0x7f6434274ac8>
BATCH_SIZE=<absl.flags._flag.Flag object at 0x7f6434274940>
CHECKPOINT_DIR=<absl.flags._flag.Flag object at 0x7f6434274a20>
F=<absl.flags._flag.Flag object at 0x7f6434274b70>
LOG_DEVICE_PLACEMENT=<absl.flags._flag.BooleanFlag object at 0x7f6434274b00>


Evaluating...

INFO:tensorflow:Restoring parameters from /home/alexander_mpa/capstone/Parlancr/models/classifier/runs/1533583054/checkpoints/model-50100
Accuracy on style test set: 45.83%
             precision    recall  f1-score   support

     normal       0.50      0.49      0.49        37
     simple       0.47      0.49      0.48        35

avg / total       0.49      0.49      0.49        72

